# **\[SOLAR\]** SIMULATION Tutorial

JiyunLim  
2023-08-09

## Data

In [11]:
import pandas as pd
import numpy as np
import os

In [4]:
# read dataframe 
df = pd.read_csv('data_eng_230710.csv')

# make y, y_upper, y_period, time, regions 
y = df.loc[:,'Bukchoncheon':'Gyeongju-si'].to_numpy()
yU = df.loc[:,'Bukchoncheon_Upper':'Gyeongju-si_Upper'].to_numpy()
yP = np.divide(y, yU+1e-10)
t = df.loc[:,'date']
regions = list(df.loc[:,'Bukchoncheon':'Gyeongju-si'].columns)

TRAIN_RATIO = 0.8
T,N = len(t),len(regions) 
LEN_TEST = int(np.floor(T*(1-TRAIN_RATIO)))
LEN_TR = T - LEN_TEST

## GConvGRU

In [5]:
%run model/gconvgru

In [6]:
s = Simulator()

In [7]:
class GConv_GRU(torch.nn.Module):
    def __init__(self, node_features, filters):
        super(GConv_GRU, self).__init__()
        self.recurrent = GConvGRU(node_features, filters, 2)
        self.linear = torch.nn.Linear(filters, 1)

    def forward(self, x, edge_index, edge_weight):
        h = self.recurrent(x, edge_index, edge_weight)
        h = F.relu(h)
        h = self.linear(h)
        return h

In [9]:
s.simulate(
    n_iteration = 1,
    lags = [1],
    filters = [1],
    epoch = [1],
    Model = GConv_GRU
)

method:classic lag:1 filters:1 epoch:1 is done
method:proposed lag:1 filters:1 epoch:1 is done
save results

In [12]:
fnames = ['./results/'+l for l in os.listdir('./results/') if l[0] != '.']
fnames 

## GConvLSTM / GCLSTM / LRGCN

In [13]:
%run model/lstm

In [14]:
s1 = Simulator()
s2 = Simulator()
s3 = Simulator()

In [15]:
class GConv_LSTM(torch.nn.Module):
    def __init__(self, node_features, filters):
        super(GConv_LSTM, self).__init__()
        self.recurrent = GConvLSTM(in_channels = node_features, out_channels = filters, K = 2)
        self.linear = torch.nn.Linear(filters, 1)

    def forward(self, x, edge_index, edge_weight, h, c):
        h_0, c_0 = self.recurrent(x, edge_index, edge_weight, h, c)
        h = F.relu(h_0)
        h = self.linear(h)
        return h, h_0, c_0

In [16]:
class GC_LSTM(torch.nn.Module):
    def __init__(self, node_features, filters):
        super(GC_LSTM, self).__init__()
        self.recurrent = GCLSTM(node_features, filters, 2)
        self.linear = torch.nn.Linear(filters, 1)

    def forward(self, x, edge_index, edge_weight, h, c):
        h_0, c_0 = self.recurrent(x, edge_index, edge_weight, h, c)
        h = F.relu(h_0)
        h = self.linear(h)
        return h, h_0, c_0

In [17]:
class LR_GCN(torch.nn.Module):
    def __init__(self, node_features, filters):
        super(LR_GCN, self).__init__()
        self.recurrent = LRGCN(node_features, filters, 1, 1)
        self.linear = torch.nn.Linear(filters, 1)

    def forward(self, x, edge_index, edge_weight, h_0, c_0):
        h_0, c_0 = self.recurrent(x, edge_index, edge_weight, h_0, c_0)
        h = F.relu(h_0)
        h = self.linear(h)
        return h, h_0, c_0

In [18]:
s1.simulate(
    n_iteration = 1,
    lags = [1],
    filters = [1],
    epoch = [1],
    Model = GConv_LSTM
)

s2.simulate(
    n_iteration = 1,
    lags = [1],
    filters = [1],
    epoch = [1],
    Model = GC_LSTM
)

s3.simulate(
    n_iteration = 1,
    lags = [1],
    filters = [1],
    epoch = [1],
    Model = LR_GCN
)

method:classic lag:1 filters:1 epoch:1 is done
method:proposed lag:1 filters:1 epoch:1 is done
save results
method:classic lag:1 filters:1 epoch:1 is done
method:proposed lag:1 filters:1 epoch:1 is done
save results
method:classic lag:1 filters:1 epoch:1 is done
method:proposed lag:1 filters:1 epoch:1 is done
save results

In [19]:
fnames = ['./results/'+l for l in os.listdir('./results/') if l[0] != '.']
fnames 

## TGCN

In [20]:
%run model/tgcn

In [21]:
s4 = Simulator()

In [22]:
class T_GCN(torch.nn.Module):
    def __init__(self, node_features, filters):
        super(T_GCN, self).__init__()
        self.recurrent = TGCN(node_features, filters)
        self.linear = torch.nn.Linear(filters, 1)

    def forward(self, x, edge_index, edge_weight, prev_hidden_state):
        h = self.recurrent(x, edge_index, edge_weight, prev_hidden_state)
        y = F.relu(h)
        y = self.linear(y)
        return y, h

In [23]:
s4.simulate(
    n_iteration = 1,
    lags = [1],
    filters = [1],
    epoch = [1],
    Model = T_GCN
)

method:classic lag:1 filters:1 epoch:1 is done
method:proposed lag:1 filters:1 epoch:1 is done
save results

In [24]:
fnames = ['./results/'+l for l in os.listdir('./results/') if l[0] != '.']
fnames 

## DCRNN

In [29]:
%run model/dcrnn

In [30]:
s5 = Simulator()

In [31]:
class DC_RNN(torch.nn.Module):
    def __init__(self, node_features, filters):
        super(DC_RNN, self).__init__()
        self.recurrent = DCRNN(node_features, filters, 2)
        self.linear = torch.nn.Linear(filters, 1)

    def forward(self, x, edge_index, edge_weight):
        h = self.recurrent(x, edge_index, edge_weight)
        h = F.relu(h)
        h = self.linear(h)
        return h

In [32]:
s5.simulate(
    n_iteration = 1,
    lags = [1],
    filters = [1],
    epoch = [1],
    Model = DC_RNN
)

method:classic lag:1 filters:1 epoch:1 is done
method:proposed lag:1 filters:1 epoch:1 is done
save results

In [34]:
fnames = ['./results/'+l for l in os.listdir('./results/') if l[0] != '.']
fnames 

In [35]:
df_ = pd.concat([pd.read_csv(fname) for fname in fnames]).reset_index(drop=True)

In [37]:
df_

In [38]:
df_.groupby(by=['model','method']).agg({'mse':[np.mean]})